In [ ]:
from bs4 import BeautifulSoup
import requests
import pandas as pd
import numpy as np
from time import sleep
import re

In [5]:
url= "https://www.billboard.com/charts/hot-100"

response = requests.get(url)
response.status_code # 200 status code means OK!

soup = BeautifulSoup(response.content, "html.parser")
soup

<!DOCTYPE html>

<html class="" lang="">
<head>
<meta charset="utf-8"/>
<meta content="IE=edge" http-equiv="X-UA-Compatible"/>
<meta content="width=device-width, initial-scale=1, user-scalable=no" name="viewport"/>
<title>The Hot 100 Chart | Billboard</title>
<meta content="The Hot 100 Chart" name="title" property="title">
<meta content="@billboard" name="twitter:site"/>
<meta content="Billboard" property="og:site_name">
<meta content="article" property="og:type">
<link href="/manifest.json" rel="manifest"/>
<style>
        .chart-pro-access {
            background-image: url('https://www.billboard.com/assets/1613666598/images/piano/chart-pro-access-mb.png?de0ea14ff29b3baaf8da');
        }

        @media (min-width: 769px) {
            .chart-pro-access {
                background-image: url('https://www.billboard.com/assets/1613666598/images/piano/chart-pro-access-dk.png?de0ea14ff29b3baaf8da');
            }
        }
    </style>
<script async="async" data-cfasync="false" src="ht

In [13]:
soup.select(".chart-list__elements")

[<ol class="chart-list__elements">
 <li class="chart-list__element display--flex">
 <button class="chart-element__wrapper display--flex flex--grow sort--default">
 <span class="chart-element__rank flex--column flex--xy-center flex--no-shrink">
 <span class="chart-element__rank__number">1</span>
 <span class="chart-element__trend chart-element__trend--steady color--secondary"><i class="fa fa-arrow-right"><span class="sr--only">Steady</span></i></span>
 </span>
 <span class="chart-element__information">
 <span class="chart-element__information__song text--truncate color--primary">Drivers License</span>
 <span class="chart-element__information__artist text--truncate color--secondary">Olivia Rodrigo</span>
 <span class="chart-element__information__delta color--secondary">
 <span class="chart-element__information__delta__text text--default">-</span>
 <span class="chart-element__information__delta__text text--last">1 Last Week</span>
 <span class="chart-element__information__delta__text text

In [20]:
soup.select(".chart-element__information")

[<span class="chart-element__information">
 <span class="chart-element__information__song text--truncate color--primary">Drivers License</span>
 <span class="chart-element__information__artist text--truncate color--secondary">Olivia Rodrigo</span>
 <span class="chart-element__information__delta color--secondary">
 <span class="chart-element__information__delta__text text--default">-</span>
 <span class="chart-element__information__delta__text text--last">1 Last Week</span>
 <span class="chart-element__information__delta__text text--peak">1 Peak Rank</span>
 <span class="chart-element__information__delta__text text--week">5 Weeks on Chart</span>
 </span>
 </span>,
 <span class="chart-element__information">
 <span class="chart-element__information__song text--truncate color--primary">Up</span>
 <span class="chart-element__information__artist text--truncate color--secondary">Cardi B</span>
 <span class="chart-element__information__delta color--secondary">
 <span class="chart-element__info

In [21]:
len(soup.select(".chart-element__information"))

100

In [28]:
soup.select(".chart-element__information")[0]
soup.select(".chart-element__information")[0].get_text().split("\n")

['',
 'Drivers License',
 'Olivia Rodrigo',
 '',
 '-',
 '1 Last Week',
 '1 Peak Rank',
 '5 Weeks on Chart',
 '',
 '']

In [26]:
soup.select(".chart-element__information")[1]
soup.select(".chart-element__information")[1].get_text().split("\n")

['',
 'Up',
 'Cardi B',
 '',
 '-',
 '- Last Week',
 '2 Peak Rank',
 '1 Weeks on Chart',
 '',
 '']

In [56]:
hot=[]
title = []
artist = []
last_week = []
peak_rank =[]
weeks_on_chart =[]

for i in range(len(soup.select(".chart-element__information"))):
    append_list=soup.select(".chart-element__information")[i].get_text().split("\n")
    hot.append(i+1)
    title.append(append_list[1])
    artist.append(append_list[2])
    last_week.append(append_list[5])
    peak_rank.append(append_list[6])
    weeks_on_chart.append(append_list[7])

In [57]:
len(title)
len(artist)
len(last_week)
len(peak_rank)

100

In [58]:
charts = pd.DataFrame({"hot":hot,"title":title,
                       "artist":artist,
                       "last_week":last_week,
                       "peak_rank": peak_rank,
                       "weeks_on_chart":weeks_on_chart
                      })

charts.head()

hot            title                        artist    last_week  \
0    1  Drivers License                Olivia Rodrigo  1 Last Week   
1    2               Up                       Cardi B  - Last Week   
2    3  Blinding Lights                    The Weeknd  3 Last Week   
3    4  Save Your Tears                    The Weeknd  8 Last Week   
4    5             Mood  24kGoldn Featuring iann dior  2 Last Week   

     peak_rank     weeks_on_chart  
0  1 Peak Rank   5 Weeks on Chart  
1  2 Peak Rank   1 Weeks on Chart  
2  1 Peak Rank  62 Weeks on Chart  
3  4 Peak Rank   9 Weeks on Chart  
4  1 Peak Rank  27 Weeks on Chart

In [59]:
pattern=re.compile("\d+")

charts["weeks_on_chart"]=charts["weeks_on_chart"].apply(lambda x: int(pattern.search(x).group(0)))
charts["peak_rank"]=charts["peak_rank"].apply(lambda x: int(pattern.search(x).group(0)))
charts["last_week"]=list(map(lambda x: x.replace(" Last Week",""),charts["last_week"]))

In [60]:
charts

hot            title                          artist last_week  peak_rank  \
0     1  Drivers License                  Olivia Rodrigo         1          1   
1     2               Up                         Cardi B         -          2   
2     3  Blinding Lights                      The Weeknd         3          1   
3     4  Save Your Tears                      The Weeknd         8          4   
4     5             Mood    24kGoldn Featuring iann dior         2          1   
..  ...              ...                             ...       ...        ...   
95   96    Almost Maybes                    Jordan Davis        99         95   
96   97      Masterpiece                          DaBaby         -         55   
97   98         Prisoner  Miley Cyrus Featuring Dua Lipa        97         54   
98   99             Skin               Sabrina Carpenter        89         48   
99  100        Quicksand                          Morray         -        100   

    weeks_on_chart  
0                5  
1                1  
2               62  
3                9  
4               27  
..             ...  
95               3  
96               3  
97              12  
98               3  
99               1  

[100 rows x 6 columns]

In [61]:
url= "https://charts.youtube.com/charts/TopVideos/global?hl=de"

response = requests.get(url)
response.status_code # 200 status code means OK!

soup = BeautifulSoup(response.content, "html.parser")
soup

<!DOCTYPE html>
<html dir="ltr" lang="de-DE"><head><script nonce="sHWeg3u8J21D9FDsuvKGIQ">var ytcsi={gt:function(n){n=(n||"")+"data_";return ytcsi[n]||(ytcsi[n]={tick:{},info:{}})},now:window.performance&&window.performance.timing&&window.performance.now&&window.performance.timing.navigationStart?function(){return window.performance.timing.navigationStart+window.performance.now()}:function(){return(new Date).getTime()},tick:function(l,t,n){var ticks=ytcsi.gt(n).tick;var v=t||ytcsi.now();if(ticks[l]){ticks["_"+l]=ticks["_"+l]||[ticks[l]];ticks["_"+l].push(v)}ticks[l]=v},info:function(k,
v,n){ytcsi.gt(n).info[k]=v},setStart:function(s,t,n){ytcsi.info("yt_sts",s,n);ytcsi.tick("_start",t,n)}};
(function(w,d){ytcsi.setStart("dhs",w.performance?w.performance.timing.responseStart:null);var isPrerender=(d.visibilityState||d.webkitVisibilityState)=="prerender";var vName=!d.visibilityState&&d.webkitVisibilityState?"webkitvisibilitychange":"visibilitychange";if(isPrerender){ytcsi.info("prerender"

In [148]:
from bs4 import BeautifulSoup
import requests
import csv

source = requests.get("http://www.mtv.de/charts/h5hl40/most-wanted-2000").text
soup = BeautifulSoup(source, 'lxml')
soup

<!DOCTYPE html>
<html class="no-js">
<head>
<!-- Dynamically generated headers -->
<title>Most Wanted 2000's - Musik Charts | MTV Germany</title>
<meta content="Bleibt up to date und seht als erstes die offiziellen deutschen Charts. Wir bieten euch alles zu den aktuellen Charts: Top 100 Single Charts, Top 100 Album Charts, Hip Hop Charts, und viele mehr." name="description"/>
<meta content="text/html; charset=utf-8" http-equiv="Content-Type"/><script type="text/javascript">(window.NREUM||(NREUM={})).loader_config={licenseKey:"1ac7d5dd09",applicationID:"81049873"};window.NREUM||(NREUM={}),__nr_require=function(e,t,n){function r(n){if(!t[n]){var i=t[n]={exports:{}};e[n][0].call(i.exports,function(t){var i=e[n][1][t];return r(i||t)},i,i.exports)}return t[n].exports}if("function"==typeof __nr_require)return __nr_require;for(var i=0;i<n.length;i++)r(n[i]);return r}({1:[function(e,t,n){function r(){}function i(e,t,n){return function(){return o(e,[u.now()].concat(c(arguments)),t?null:this,n),

In [78]:
len(soup.select("div.chartItemsBox"))

20

In [94]:
top_2000

[<div class="chartItemTitle"><div class="videoTitle">In The End</div><a class="artist artistLinked regular-content" href="http://www.mtv.de/kuenstler/zlkj9f/linkin-park"><span>Linkin Park</span></a></div>,
 <div class="chartItemTitle"><div class="videoTitle">Numb</div><a class="artist artistLinked regular-content" href="http://www.mtv.de/kuenstler/zlkj9f/linkin-park"><span>Linkin Park</span></a></div>,
 <div class="chartItemTitle"><div class="videoTitle">Mr. Brightside</div><a class="artist artistLinked regular-content" href="http://www.mtv.de/kuenstler/ymc2jf/the-killers"><span>The Killers</span></a></div>,
 <div class="chartItemTitle"><div class="videoTitle">Last Resort</div><a class="artist artistLinked regular-content" href="http://www.mtv.de/kuenstler/todply/papa-roach"><span>Papa Roach</span></a></div>,
 <div class="chartItemTitle"><div class="videoTitle">Lose Yourself</div><div class="artist regular-content">Eminem</div></div>,
 <div class="chartItemTitle"><div class="videoTitle

In [134]:
top_2000=soup.select("div.chartItemTitle")
title=[]
artist=[]

for i in range(len(top_2000)):
    try:
        title.append(top_2000[i].find("div",{"class":"videoTitle"}).get_text())
    #print(title[-1])
    except:
        title.append("NA")
        
    try:
        artist.append(top_2000[i].find("div",{"class":"artist regular-content"}).get_text())
        #print("if")
    except:
        try:
            artist.append(top_2000[i].find("a",{"class":"artist artistLinked regular-content"}).get_text())
            #print("else")
        except:
            artist.append("NA")

In [135]:
title

['In The End',
 'Numb',
 'Mr. Brightside',
 'Last Resort',
 'Lose Yourself',
 'Without Me',
 'Low',
 'Monsta',
 'Hamma!',
 'Yeah!',
 'Ding',
 'Everytime We Touch',
 'Another One Bites The Dust',
 'Candy Shop',
 'In Da Club',
 'Schlechtes Vorbild',
 'How You Remind Me',
 'Tik Tok',
 'I Gotta Feeling',
 'Alles neu']

In [136]:
artist

['Linkin Park',
 'Linkin Park',
 'The Killers',
 'Papa Roach',
 'Eminem',
 'Eminem',
 'Flo Rida',
 'Culcha Candela',
 'Culcha Candela',
 'Ludacris',
 'Seeed',
 'Cascada',
 'Queen vs the Miami Project',
 '50 Cent',
 '50 Cent',
 'Mr. Hurley & Die Pulveraffen',
 'Nickelback',
 'Ke$ha',
 'Black Eyed Peas',
 'Peter Fox']

In [177]:
url= "http://www.mtv.de/charts/h5hl40/most-wanted-2000"

def mtv_scrap(url):
    
    response = requests.get(url)
    response.status_code # 200 status code means OK!

    soup = BeautifulSoup(response.content, "html.parser")
    
    top_2000=soup.select("div.chartItemTitle")
    title=[]
    artist=[]

    for i in range(len(top_2000)):
        try:
            title.append(top_2000[i].find("div",{"class":"videoTitle"}).get_text())
    #print(title[-1])
        except:
            title.append("NA")
        
        try:
            artist.append(top_2000[i].find("div",{"class":"artist regular-content"}).get_text())
        #print("if")
        except:
            try:
                artist.append(top_2000[i].find("a",{"class":"artist artistLinked regular-content"}).get_text())
            #print("else")
            except:
                artist.append("NA")
    return title, artist

title, artist = mtv_scrap(url)

songs = pd.DataFrame({"title":title,
                       "artist":artist
                      })
def df_songs(title, artist,songs):
    songs2 = pd.DataFrame({"title":title,
                       "artist":artist
                      })
    songs=pd.concat([songs,songs2],axis=0,ignore_index=True)
    return songs

In [172]:
url="http://www.mtv.de/charts/deajvb/top-100-jahrescharts-2019"
    
title8, artist8=mtv_scrap(url)
songs=df_songs(title8, artist8,songs)

In [181]:
url="http://www.mtv.de/charts/lod2k0/top-100-jahrescharts-2020"
    
title7, artist7=mtv_scrap(url)
songs=df_songs(title7, artist7,songs)

In [ ]:
#Charts frequently updated

In [182]:
url= "http://www.mtv.de/charts/c6mc86/single-top-100"

title2, artist2=mtv_scrap(url)
songs=df_songs(title2, artist2,songs)
#songs

In [183]:
url= "http://www.mtv.de/charts/n91ory/midweek-single-top-100"

title3, artist3=mtv_scrap(url)
songs=df_songs(title3, artist3,songs)

In [184]:
url="http://www.mtv.de/charts/9gtiy5/single-trending"
    
title4, artist4=mtv_scrap(url)
songs=df_songs(title4, artist4,songs)

In [185]:
url="http://www.mtv.de/charts/h4oi23/top100-music-streaming"
    
title5, artist5=mtv_scrap(url)
songs=df_songs(title5, artist5,songs)

In [186]:
url="http://www.mtv.de/charts/pcbqpc/downloads-charts-single"
    
title6, artist6=mtv_scrap(url)
songs=df_songs(title6, artist6,songs)

In [187]:
url="http://www.mtv.de/charts/2ny5w9/dance-charts"
    
title9, artist9=mtv_scrap(url)
songs=df_songs(title9, artist9,songs)

In [188]:
url="http://www.mtv.de/charts/vh9pco/hip-hop-charts"
    
title10, artist10=mtv_scrap(url)
songs=df_songs(title10, artist10,songs)

In [191]:
songs.drop_duplicates()

title       artist
0                            In The End  Linkin Park
1                                  Numb  Linkin Park
2                        Mr. Brightside  The Killers
3                           Last Resort   Papa Roach
4                         Lose Yourself       Eminem
..                                  ...          ...
234                     Hollywood Uncut     Bonez MC
235             Music To Be Murdered By       Eminem
236                Hollywood's Bleeding  Post Malone
237                   Ich & keine Maske         Sido
238  Come Over When You're Sober, Pt. 2     Lil Peep

[121 rows x 2 columns]

In [196]:
len(songs["title"].value_counts().to_list())

118

In [ ]:
#Earthquake

In [294]:
url = "https://www.emsc-csem.org/Earthquake/"

response = requests.get(url)
response.status_code # 200 status code means OK!

soup = BeautifulSoup(response.content, "html.parser")
soup

<!DOCTYPE html PUBLIC "-//W3C//DTD XHTML 1.0 Strict//EN" "http://www.w3.org/TR/xhtml1/DTD/xhtml1-strict.dtd">

<html lang="en" xml:lang="en" xmlns="http://www.w3.org/1999/xhtml" xmlns:og="http://opengraphprotocol.org/schema/">
<head><meta content="srFzNKBTd0FbRhtnzP--Tjxl01NfbscjYwkp4yOWuQY" name="google-site-verification"/><meta content="BCAA3C04C41AE6E6AFAF117B9469C66F" name="msvalidate.01"/><meta content="43b36314ccb77957" name="y_key"/><!-- 5-Clk8f50tFFdPTU97Bw7ygWE1A -->
<meta content="en" http-equiv="Content-Language"/><meta content="text/html; charset=utf-8" http-equiv="Content-Type"/>
<meta content="all" name="robots"/>
<meta content="earthquake,earthquakes,last earthquake,earthquake today,earthquakes today,earth quake,earth quakes,real time seismicity,seismic,seismicity,seismicity map,seismology,sismologie,EMSC,CSEM,seismicity on google earth,sumatra,tsunami,tsunamis,map,maps,richter,mercalli,moment tensors,epicenter,magnitude,seismology,foreshock,aftershock,tremor" name="keyw

In [295]:
#tbody>tr>td

time=soup.select("#tbody>tr>td.tabev6 > b > a")


In [298]:
import re

In [299]:
len(time)

50

In [300]:
time=soup.select("#tbody>tr>td.tabev6 > b > a") #time is a list
date=[]
timestamp=[]

for i in range(len(time)):
    test=time[i].get_text().replace("\xa0\xa0\xa0",",")
    #print(test)
    test2=test.split(",") #return a list
    #print(test2)
    date.append(test2[0])
    timestamp.append(test2[1])

#time[1].get_text()
#timestamp

In [301]:
latitude=soup.select("#tbody>tr>td:nth-child(5)")
direction=soup.select("#tbody>tr>td:nth-child(6)")
latitudes=[]
directions1=[]

for i in range(len(latitude)):
    latitudes.append(latitude[i].get_text().replace("\xa0",""))
    directions1.append(direction[i].get_text().replace("\xa0",""))
                     
#latitudes
#directions
#\39 51700 > td:nth-child(6)

In [302]:
longitude=soup.select("#tbody>tr>td:nth-child(7)")
longitudes=[]
direction=soup.select("#tbody>tr>td:nth-child(8)")
directions2=[]

for i in range(len(longitude)):
    longitudes.append(longitude[i].get_text().replace("\xa0",""))
    directions2.append(direction[i].get_text().replace("\xa0",""))
        
#longitudes
#directions2

In [303]:
#\39 51700 > td.tabev3

depth=soup.select("#tbody>tr>td.tabev3")
depths=[]

for i in range(len(depth)):
    depths.append(depth[i].get_text())

#depths

In [304]:
#\39 51706 > #\39 51706 > td:nth-child(11)

mag=soup.select("#tbody>tr>td:nth-child(11)")
mags=[]

for i in range(len(mag)):
    mags.append(mag[i].get_text())

In [305]:
location=[]

for i in range(len(mag)):
    string=str("reg{}".format(i))
    location.append(soup.find("td",{"id":string}).get_text().replace("\xa0",""))

location

['SPAIN',
 'CENTRAL PERU',
 'MINAHASA, SULAWESI, INDONESIA',
 'CENTRAL PERU',
 'PUERTO RICO',
 'PUERTO RICO REGION',
 'AZORES-CAPE ST. VINCENT RIDGE',
 'SAN JUAN, ARGENTINA',
 'PUERTO RICO REGION',
 'SWITZERLAND',
 'PUERTO RICO REGION',
 'TARAPACA, CHILE',
 'KURIL ISLANDS',
 'NEVADA',
 'NEAR COAST OF NICARAGUA',
 'NORTHERN CALIFORNIA',
 'NEVADA',
 'SOUTHERN CALIFORNIA',
 'MINDANAO, PHILIPPINES',
 'SWITZERLAND',
 'ISLAND OF HAWAII, HAWAII',
 'MINAHASA, SULAWESI, INDONESIA',
 'WESTERN TEXAS',
 'NEAR N COAST OF PAPUA, INDONESIA',
 'OFF COAST OF CHIAPAS, MEXICO',
 'ISLAND OF HAWAII, HAWAII',
 'DOMINICAN REPUBLIC',
 'ALASKA PENINSULA',
 'DOMINICAN REPUBLIC REGION',
 'SALTA, ARGENTINA',
 'BOHOL, PHILIPPINES',
 'ISLAND OF HAWAII, HAWAII',
 'PUERTO RICO REGION',
 'ARUNACHAL PRADESH, INDIA',
 'ISLAND OF HAWAII, HAWAII',
 'NEAR COAST OF CENTRAL PERU',
 'OFFSHORE CHIAPAS, MEXICO',
 'DOMINICAN REPUBLIC',
 'SOUTHERN XINJIANG, CHINA',
 'CROATIA',
 'SUMBA REGION, INDONESIA',
 'KEPULAUAN TALAUD, INDON

In [319]:
print(len(date))
print(len(timestamp))
print(len(latitudes))
print(len(directions1))
print(len(longitudes))
print(len(directions2))
print(len(depths))
print(len(mags))
print(len(location))

50
50
50
50
50
50
50
50
50


In [306]:
final_df=pd.DataFrame({"date":date,"timestamp":timestamp,
                      "latitudes":latitudes, "direction_latitude":directions1,
                      "longitudes":longitudes, "direction_longitude":directions2,
                      "depth":depths, "magnitude":mags, "location":location})

In [307]:
final_df

date   timestamp latitudes direction_latitude longitudes  \
0   2021-02-22  19:49:03.3     37.19                  N       3.71   
1   2021-02-22  19:31:55.0      9.24                  S      74.94   
2   2021-02-22  19:22:14.5      1.30                  N     121.99   
3   2021-02-22  19:08:26.0      9.65                  S      74.88   
4   2021-02-22  19:05:36.7     18.02                  N      66.70   
5   2021-02-22  18:57:15.9     17.89                  N      66.80   
6   2021-02-22  18:53:21.0     36.65                  N      11.15   
7   2021-02-22  18:51:32.0     31.39                  S      67.94   
8   2021-02-22  18:41:38.2     17.97                  N      66.99   
9   2021-02-22  18:29:37.0     46.32                  N       7.35   
10  2021-02-22  18:19:58.1     17.91                  N      66.84   
11  2021-02-22  18:18:31.0     19.36                  S      69.41   
12  2021-02-22  18:09:57.3     45.33                  N     150.71   
13  2021-02-22  18:02:13.7     38.17                  N     117.98   
14  2021-02-22  17:57:16.0     12.34                  N      87.80   
15  2021-02-22  17:56:28.9     39.56                  N     123.47   
16  2021-02-22  17:52:37.6     38.18                  N     117.87   
17  2021-02-22  17:50:01.7     35.70                  N     117.46   
18  2021-02-22  17:48:56.0      8.58                  N     125.71   
19  2021-02-22  17:46:57.0     46.74                  N      10.16   
20  2021-02-22  17:34:31.6     19.23                  N     155.38   
21  2021-02-22  17:26:16.0      0.10                  N     123.54   
22  2021-02-22  17:20:46.4     31.73                  N     104.06   
23  2021-02-22  17:12:03.0      1.81                  S     139.51   
24  2021-02-22  17:05:35.0     14.29                  N      93.40   
25  2021-02-22  16:45:30.9     19.25                  N     155.43   
26  2021-02-22  16:39:15.0     18.43                  N      71.71   
27  2021-02-22  16:38:38.7     55.85                  N     158.26   
28  2021-02-22  16:29:32.0     20.40                  N      70.81   
29  2021-02-22  16:24:44.0     24.25                  S      66.98   
30  2021-02-22  16:11:46.0      9.81                  N     124.70   
31  2021-02-22  16:03:17.3     19.22                  N     155.41   
32  2021-02-22  15:52:13.7     18.76                  N      65.63   
33  2021-02-22  15:44:22.0     27.42                  N      92.65   
34  2021-02-22  15:30:58.8     19.18                  N     155.46   
35  2021-02-22  15:21:30.0     15.36                  S      75.83   
36  2021-02-22  15:21:22.9     14.41                  N      93.13   
37  2021-02-22  15:06:35.9     19.84                  N      71.05   
38  2021-02-22  14:57:29.2     41.47                  N      83.42   
39  2021-02-22  14:36:35.0     45.60                  N      15.95   
40  2021-02-22  14:34:14.0      9.85                  S     120.49   
41  2021-02-22  14:31:27.0      4.52                  N     127.34   
42  2021-02-22  14:09:03.0     15.54                  N      96.80   
43  2021-02-22  14:07:28.4     37.21                  N       3.69   
44  2021-02-22  14:05:26.7     36.49                  N      28.86   
45  2021-02-22  13:54:54.0     36.53                  N      28.89   
46  2021-02-22  13:54:30.0     47.72                  N     128.62   
47  2021-02-22  13:50:01.6     34.40                  N      97.41   
48  2021-02-22  13:44:03.0      8.06                  S     117.86   
49  2021-02-22  13:41:05.6     37.80                  N      26.99   

   direction_longitude depth magnitude                          location  
0                    W    10       2.1                             SPAIN  
1                    W    24       4.4                      CENTRAL PERU  
2                    E    60       5.7     MINAHASA, SULAWESI, INDONESIA  
3                    W   131       4.4                      CENTRAL PERU  
4                    W    10       2.3                       PUE

In [ ]:
#automated earthquake generation

In [321]:
urls=[]

for i in range(150):
    urls.append("https://www.emsc-csem.org/Earthquake/?view="+str(i+1))
    
#urls

In [289]:
def earthquake(url):
    response = requests.get(url)
    response.status_code # 200 status code means OK!

    soup = BeautifulSoup(response.content, "html.parser")
    
    #creating empty
    date=[]
    timestamp=[]
    latitudes=[]
    directions1=[]
    longitudes=[]
    directions2=[]
    depths=[]
    mags=[]
    location=[]
    
    time=soup.select("#tbody>tr>td.tabev6 > b > a") #time is a list
    latitude=soup.select("#tbody>tr>td:nth-child(5)")
    direction=soup.select("#tbody>tr>td:nth-child(6)")
    longitude=soup.select("#tbody>tr>td:nth-child(7)")
    direction=soup.select("#tbody>tr>td:nth-child(8)")
    depth=soup.select("#tbody>tr>td.tabev3")
    mag=soup.select("#tbody>tr>td:nth-child(11)")
    
    from time import sleep
   
    for i in range(len(time)):
        
        wait_time = np.random.randint(1,4)
        sleep(wait_time)
        
        test=time[i].get_text().replace("\xa0\xa0\xa0",",")
        test2=test.split(",") #return a list
        date.append(test2[0])
        timestamp.append(test2[1])
        latitudes.append(latitude[i].get_text().replace("\xa0",""))
        directions1.append(direction[i].get_text().replace("\xa0",""))
        longitudes.append(longitude[i].get_text().replace("\xa0",""))
        directions2.append(direction[i].get_text().replace("\xa0",""))
        depths.append(depth[i].get_text())
        mags.append(mag[i].get_text())
    
    for i in range(len(mag)):
        string=str("reg{}".format(i))
        location.append(soup.find("td",{"id":string}).get_text().replace("\xa0",""))
        
    final_df=pd.DataFrame({"date":date,"timestamp":timestamp,
                      "latitudes":latitudes, "direction_latitude":directions1,
                      "longitudes":longitudes, "direction_longitude":directions2,
                      "depth":depths, "magnitude":mags, "location":location})
        
    return final_df

In [290]:
final_df2=earthquake(urls[1])

#final_df=pd.DataFrame([final_df,final_df2],axis=0)

#final_df2

In [ ]:
#final_df=pd.DataFrame([final_df,final_df2],axis=0)
#final_df2

In [322]:
final_df=pd.concat([final_df,final_df2],axis=0,ignore_index=True)

In [326]:
final_df

date   timestamp latitudes direction_latitude longitudes  \
0    2021-02-22  19:49:03.3     37.19                  N       3.71   
1    2021-02-22  19:31:55.0      9.24                  S      74.94   
2    2021-02-22  19:22:14.5      1.30                  N     121.99   
3    2021-02-22  19:08:26.0      9.65                  S      74.88   
4    2021-02-22  19:05:36.7     18.02                  N      66.70   
..          ...         ...       ...                ...        ...   
96   2021-02-22  08:27:32.0     22.93                  W      69.01   
97   2021-02-22  08:26:14.0     14.31                  W      92.91   
98   2021-02-22  08:24:12.5     36.77                  E      28.15   
99   2021-02-22  08:21:45.0     36.70                  W      11.35   
100  2021-02-22  08:21:30.0      2.63                  E     128.85   

    direction_longitude depth magnitude                          location  
0                     W    10       2.1                             SPAIN  
1                     W    24       4.4                      CENTRAL PERU  
2                     E    60       5.7     MINAHASA, SULAWESI, INDONESIA  
3                     W   131       4.4                      CENTRAL PERU  
4                     W    10       2.3                       PUERTO RICO  
..                  ...   ...       ...                               ...  
96                    W   105       2.8                ANTOFAGASTA, CHILE  
97                    W    15       3.8          OFFSHORE CHIAPAS, MEXICO  
98                    E    64       2.3  DODECANESE IS.-TURKEY BORDER REG  
99                    W    31       2.1     AZORES-CAPE ST. VINCENT RIDGE  
100                   E    10       3.3              CERAM SEA, INDONESIA  

[101 rows x 9 columns]

In [327]:
#this will take hours FYI

for i in range(3,10):
    final_df2=earthquake(urls[i])
    final_df=pd.concat([final_df,final_df2],axis=0,ignore_index=True)

#final_df2=earthquake(urls[1])

In [328]:
final_df

date   timestamp latitudes direction_latitude longitudes  \
0    2021-02-22  19:49:03.3     37.19                  N       3.71   
1    2021-02-22  19:31:55.0      9.24                  S      74.94   
2    2021-02-22  19:22:14.5      1.30                  N     121.99   
3    2021-02-22  19:08:26.0      9.65                  S      74.88   
4    2021-02-22  19:05:36.7     18.02                  N      66.70   
..          ...         ...       ...                ...        ...   
453  2021-02-20  06:49:01.3     35.64                  W     117.45   
454  2021-02-20  06:48:44.0     17.82                  W      68.30   
455  2021-02-20  06:45:07.0     31.36                  W      68.70   
456  2021-02-20  06:44:14.0     24.06                  W     108.48   
457  2021-02-20  06:41:54.8     19.21                  W     155.44   

    direction_longitude depth magnitude                       location  
0                     W    10       2.1                          SPAIN  
1                     W    24       4.4                   CENTRAL PERU  
2                     E    60       5.7  MINAHASA, SULAWESI, INDONESIA  
3                     W   131       4.4                   CENTRAL PERU  
4                     W    10       2.3                    PUERTO RICO  
..                  ...   ...       ...                            ...  
453                   W     5       2.0            SOUTHERN CALIFORNIA  
454                   W    50       2.8      DOMINICAN REPUBLIC REGION  
455                   W    93       3.0            SAN JUAN, ARGENTINA  
456                   W    10       4.0             GULF OF CALIFORNIA  
457                   W    34       2.2       ISLAND OF HAWAII, HAWAII  

[458 rows x 9 columns]